# Set up environment

In [1]:
#pip install pandas scipy matplotlib imageio cv2 opencv-python torch pyyaml tqdm torchvision seaborn

In [1]:
# import relevant libraries
from IPython.display import Image
import pandas as pd
import random
import os
import glob
import shutil
from scipy import ndimage
import matplotlib.pyplot as plt
import imageio
import json
import numpy as np
import cv2

In [2]:
%cd ../5_train_yolo_tooth_segmentation

C:\Users\dental-1\Documents\dent_seg\5_train_yolo_initial_tooth_segmentation


In [3]:
# remote yolov5 folder
#!rm -r 'C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/yolov5'

In [4]:
# clone repo
if os.path.exists('C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/yolov5/') == False:
    !git clone https://github.com/ultralytics/yolov5
    %cd yolov5
else:
    %cd yolov5
    !git init
    !git pull https://github.com/ultralytics/yolov5

fatal: not a git repository (or any of the parent directories): .git


In [6]:
# install dependencies
if os.path.exists('C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/yolov5/') == False:
    !pip install -r yolov5/requirements.txt

In [7]:
import torch
print('Setup complete. Using torch %s %s' % (torch.__version__, torch.cuda.get_device_properties(0) if torch.cuda.is_available() else 'CPU'))

Setup complete. Using torch 1.9.1+cu102 _CudaDeviceProperties(name='Quadro RTX 8000', major=7, minor=5, total_memory=49152MB, multi_processor_count=72)


# Set up data

In [8]:
# remote data folder
#!rm -r 'C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/data'
#!rm -r 'C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/unseen_images'

In [9]:
# prepare data directory structure for Yolo
path = 'C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/'

if os.path.exists(path + 'data/') == False:
    os.mkdir(path + 'data/')
    os.mkdir(path + 'data/images/')
    os.mkdir(path + 'data/images/test')
    os.mkdir(path + 'data/images/train')
    os.mkdir(path + 'data/images/valid/')
    os.mkdir(path + 'data/labels/')
    os.mkdir(path + 'data/labels/test')
    os.mkdir(path + 'data/labels/train')
    os.mkdir(path + 'data/labels/valid/')
    os.mkdir(path + 'unseen_images/')

In [10]:
# define variables
path = 'C:/Users/dental-1/Documents/dent_seg/'
folder = '5_train_yolo_tooth_segmentation/'
bounding_boxes = os.listdir(path + folder + '/bounding_boxes')
images_jpg = glob.glob(path + '2_dental_images/raw_images/*.jpg')
image_png = glob.glob(path + '2_dental_images/raw_images/*.png')
random.seed(1234)
norm = np.zeros((800,800))
image_names = []

for img in images_jpg:
    image_names.append(img.split('\\')[-1].split('.')[0])
    
for img in image_png:
    image_names.append(img.split('\\')[1][:-4])

In [11]:
# define function to organise data
def setup_data(bounding_boxes):   
    for bb in bounding_boxes:
        if 'cate' in bb:
            file_type = '.jpg'
        else:
            file_type = '.png'
        
        if bb.split('.txt')[0] in image_names:
            image_path = path + '2_dental_images/raw_images/' + bb.split('.txt')[0] + file_type
            source = path + folder + '/bounding_boxes/' + bb
            # normalise image
            unnorm_img = imageio.imread(image_path, as_gray=True)
            normalized_img = cv2.normalize(unnorm_img, norm, 0, 255, cv2.NORM_MINMAX)
            if random.random() > 0.3:
                destination = path + folder + '/data/labels/train/' + bb
                shutil.copy(source, destination)
                # copy image to its respective folder
                cv2.imwrite(path + folder + '/data/images/train/' + bb.split('.txt')[0] + file_type, normalized_img)
            else:
                # assign test data to proper location
                destination_test = path + folder + '/data/labels/test/' + bb
                shutil.copy(source, destination_test)
                # copy image to its respective folder
                cv2.imwrite(path + folder + '/data/images/test/' + bb.split('.txt')[0] + file_type, normalized_img)
                # validation housekeeping
                destination_val = path + folder + '/data/labels/valid/' + bb
                shutil.copy(source, destination_val)
                # copy image to its respective folder
                cv2.imwrite(path + folder + '/data/images/valid/' + bb.split('.txt')[0] + file_type, normalized_img)
            image_names.remove(bb.split('.txt')[0]) 
    for image in image_names:
        if 'cate' in image:
            image_path = path + '2_dental_images/raw_images/' + image + '.jpg'
        else:
            image_path = path + '2_dental_images/raw_images/' + image + '.png'
        # normalise image
        unnorm_img = imageio.imread(image_path, as_gray=True)
        normalized_img = cv2.normalize(unnorm_img, norm, 0, 255, cv2.NORM_MINMAX)
        # copy image to its respective folder
        if 'cate' in image:
            cv2.imwrite(path + folder + '/unseen_images/' + image +'.jpg', normalized_img)
        else:
            cv2.imwrite(path + folder + '/unseen_images/' + image +'.png', normalized_img)

In [12]:
# populate folders
if len(os.listdir(path + folder + '/data/images/test')) <= 1:
    setup_data(bounding_boxes)

# Configure YAML files

In [13]:
with open('model_yaml', 'w+') as file:
    file.write(
        """
        # parameters
        nc: 1  # number of classes
        depth_multiple: 0.33  # model depth multiple
        width_multiple: 0.50  # layer channel multiple

        # anchors
        anchors:
          - [10,13, 16,30, 33,23]  # P3/8
          - [30,61, 62,45, 59,119]  # P4/16
          - [116,90, 156,198, 373,326]  # P5/32

        # YOLOv5 backbone
        backbone:
          # [from, number, module, args]
          [[-1, 1, Focus, [64, 3]],  # 0-P1/2
           [-1, 1, Conv, [128, 3, 2]],  # 1-P2/4
           [-1, 3, BottleneckCSP, [128]],
           [-1, 1, Conv, [256, 3, 2]],  # 3-P3/8
           [-1, 9, BottleneckCSP, [256]],
           [-1, 1, Conv, [512, 3, 2]],  # 5-P4/16
           [-1, 9, BottleneckCSP, [512]],
           [-1, 1, Conv, [1024, 3, 2]],  # 7-P5/32
           [-1, 1, SPP, [1024, [5, 9, 13]]],
           [-1, 3, BottleneckCSP, [1024, False]],  # 9
          ]

        # YOLOv5 head
        head:
          [[-1, 1, Conv, [512, 1, 1]],
           [-1, 1, nn.Upsample, [None, 2, 'nearest']],
           [[-1, 6], 1, Concat, [1]],  # cat backbone P4
           [-1, 3, BottleneckCSP, [512, False]],  # 13

           [-1, 1, Conv, [256, 1, 1]],
           [-1, 1, nn.Upsample, [None, 2, 'nearest']],
           [[-1, 4], 1, Concat, [1]],  # cat backbone P3
           [-1, 3, BottleneckCSP, [256, False]],  # 17 (P3/8-small)

           [-1, 1, Conv, [256, 3, 2]],
           [[-1, 14], 1, Concat, [1]],  # cat head P4
           [-1, 3, BottleneckCSP, [512, False]],  # 20 (P4/16-medium)

           [-1, 1, Conv, [512, 3, 2]],
           [[-1, 10], 1, Concat, [1]],  # cat head P5
           [-1, 3, BottleneckCSP, [1024, False]],  # 23 (P5/32-large)

           [[17, 20, 23], 1, Detect, [nc, anchors]],  # Detect(P3, P4, P5)
          ]
        """
    )

In [14]:
with open('data_yaml', 'w+') as file:
    file.write(
        """
        train: C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/data/images/train
        val: C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/data/images/valid
        test: C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/data/images/test

        nc: 1
        names: ['tooth']
        """
    )

# Train model

In [15]:
%%time
!python train.py --batch 16 --epochs 500 --data data_yaml --cfg model_yaml --weights ../../4_weights/IANN_initial_weight.pt --patience 50 --name teeth --cache

github:  YOLOv5 is out of date by 30 commits. Use `git pull` or `git clone https://github.com/ultralytics/yolov5` to update.
Weights & Biases: run 'pip install wandb' to automatically track and visualize YOLOv5  runs (RECOMMENDED)
Plotting labels... 

autoanchor: Analyzing anchors... anchors/target = 5.65, Best Possible Recall (BPR) = 1.0000
Optimizer stripped from runs\train\teeth4\weights\last.pt, 14.8MB
Optimizer stripped from runs\train\teeth4\weights\best.pt, 14.8MB
Wall time: 57min 49s


train: weights=../../4_weights/IANN_initial_weight.pt, cfg=model_yaml, data=data_yaml, hyp=data\hyps\hyp.scratch.yaml, epochs=500, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, adam=False, sync_bn=False, workers=8, project=runs\train, name=teeth, exist_ok=False, quad=False, linear_lr=False, label_smoothing=0.0, patience=50, freeze=0, save_period=-1, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
YOLOv5  v6.0-53-g5866646 torch 1.9.1+cu102 CUDA:0 (Quadro RTX 8000, 49152MiB)

hyperparameters: lr0=0.01, lrf=0.1, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl_gamma=0.0, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, degrees=0.0, translate=0.1, scale=0.5, shear=0.0, perspective=0.0, 

     3/499     2.47G   0.07487    0.1853         0       657       640:  92%|#########2| 46/50 [00:06<00:00,  7.78it/s]
     3/499     2.47G    0.0748    0.1849         0       686       640:  92%|#########2| 46/50 [00:06<00:00,  7.78it/s]
     3/499     2.47G    0.0748    0.1849         0       686       640:  94%|#########3| 47/50 [00:06<00:00,  7.57it/s]
     3/499     2.47G   0.07473    0.1854         0       894       640:  94%|#########3| 47/50 [00:06<00:00,  7.57it/s]
     3/499     2.47G   0.07473    0.1854         0       894       640:  96%|#########6| 48/50 [00:06<00:00,  7.69it/s]
     3/499     2.47G   0.07465    0.1859         0       881       640:  96%|#########6| 48/50 [00:06<00:00,  7.69it/s]
     3/499     2.47G   0.07465    0.1859         0       881       640:  98%|#########8| 49/50 [00:06<00:00,  7.51it/s]
     3/499     2.47G   0.07448    0.1855         0       207       640:  98%|#########8| 49/50 [00:06<00:00,  7.51it/s]
     3/499     2.47G   0.07448    0.1855

     7/499     2.47G   0.05938    0.1735         0       661       640:  74%|#######4  | 37/50 [00:04<00:01,  7.48it/s]
     7/499     2.47G   0.05938    0.1735         0       661       640:  76%|#######6  | 38/50 [00:04<00:01,  7.63it/s]
     7/499     2.47G    0.0593    0.1732         0       721       640:  76%|#######6  | 38/50 [00:05<00:01,  7.63it/s]
     7/499     2.47G    0.0593    0.1732         0       721       640:  78%|#######8  | 39/50 [00:05<00:01,  7.40it/s]
     7/499     2.47G   0.05933    0.1739         0       926       640:  78%|#######8  | 39/50 [00:05<00:01,  7.40it/s]
     7/499     2.47G   0.05933    0.1739         0       926       640:  80%|########  | 40/50 [00:05<00:01,  7.85it/s]
     7/499     2.47G   0.05924    0.1738         0       781       640:  80%|########  | 40/50 [00:05<00:01,  7.85it/s]
     7/499     2.47G   0.05924    0.1738         0       781       640:  82%|########2 | 41/50 [00:05<00:01,  7.61it/s]
     7/499     2.47G   0.05915    0.1737

    24/499     2.47G   0.04392    0.1359         0       653       640:  80%|########  | 40/50 [00:05<00:01,  7.90it/s]
    24/499     2.47G   0.04396    0.1361         0       826       640:  80%|########  | 40/50 [00:05<00:01,  7.90it/s]
    24/499     2.47G   0.04396    0.1361         0       826       640:  82%|########2 | 41/50 [00:05<00:01,  8.20it/s]
    24/499     2.47G   0.04399    0.1362         0       759       640:  82%|########2 | 41/50 [00:05<00:01,  8.20it/s]
    24/499     2.47G   0.04399    0.1362         0       759       640:  84%|########4 | 42/50 [00:05<00:01,  7.84it/s]
    24/499     2.47G   0.04399    0.1366         0       854       640:  84%|########4 | 42/50 [00:05<00:01,  7.84it/s]
    24/499     2.47G   0.04399    0.1366         0       854       640:  86%|########6 | 43/50 [00:05<00:00,  7.89it/s]
    24/499     2.47G   0.04398    0.1365         0       757       640:  86%|########6 | 43/50 [00:05<00:00,  7.89it/s]
    24/499     2.47G   0.04398    0.1365

...

   257/499     2.47G   0.03302    0.1197         0      1049       640:   6%|6         | 3/50 [00:00<00:08,  5.85it/s]
   257/499     2.47G   0.03287    0.1148         0       778       640:   6%|6         | 3/50 [00:00<00:08,  5.85it/s]
   257/499     2.47G   0.03287    0.1148         0       778       640:   8%|8         | 4/50 [00:00<00:07,  5.80it/s]
   257/499     2.47G   0.03311    0.1098         0       676       640:   8%|8         | 4/50 [00:00<00:07,  5.80it/s]
   257/499     2.47G   0.03311    0.1098         0       676       640:  10%|#         | 5/50 [00:00<00:07,  5.81it/s]
   257/499     2.47G   0.03231    0.1059         0       628       640:  10%|#         | 5/50 [00:01<00:07,  5.81it/s]
   257/499     2.47G   0.03231    0.1059         0       628       640:  12%|#2        | 6/50 [00:01<00:08,  5.47it/s]
   257/499     2.47G   0.03252    0.1071         0       904       640:  12%|#2        | 6/50 [00:01<00:08,  5.47it/s]
   257/499     2.47G   0.03252    0.1071        

   284/499     2.47G   0.03107    0.0988         0       766       640:  14%|#4        | 7/50 [00:01<00:07,  5.97it/s]
   284/499     2.47G   0.03107    0.0988         0       766       640:  16%|#6        | 8/50 [00:01<00:07,  5.75it/s]
   284/499     2.47G   0.03087   0.09585         0       543       640:  16%|#6        | 8/50 [00:01<00:07,  5.75it/s]
   284/499     2.47G   0.03087   0.09585         0       543       640:  18%|#8        | 9/50 [00:01<00:06,  6.12it/s]
   284/499     2.47G   0.03119   0.09662         0       808       640:  18%|#8        | 9/50 [00:01<00:06,  6.12it/s]
   284/499     2.47G   0.03119   0.09662         0       808       640:  20%|##        | 10/50 [00:01<00:07,  5.54it/s]
   284/499     2.47G   0.03151    0.0971         0       795       640:  20%|##        | 10/50 [00:01<00:07,  5.54it/s]
   284/499     2.47G   0.03151    0.0971         0       795       640:  22%|##2       | 11/50 [00:01<00:06,  5.62it/s]
   284/499     2.47G   0.03127   0.09668     

   310/499     2.47G   0.03128    0.1002         0       826       640:  68%|######8   | 34/50 [00:05<00:02,  5.67it/s]
   310/499     2.47G   0.03132    0.1004         0       790       640:  68%|######8   | 34/50 [00:06<00:02,  5.67it/s]
   310/499     2.47G   0.03132    0.1004         0       790       640:  70%|#######   | 35/50 [00:06<00:02,  5.42it/s]
   310/499     2.47G   0.03126    0.1003         0       708       640:  70%|#######   | 35/50 [00:06<00:02,  5.42it/s]
   310/499     2.47G   0.03126    0.1003         0       708       640:  72%|#######2  | 36/50 [00:06<00:02,  5.96it/s]
   310/499     2.47G    0.0313    0.1004         0       873       640:  72%|#######2  | 36/50 [00:06<00:02,  5.96it/s]
   310/499     2.47G    0.0313    0.1004         0       873       640:  74%|#######4  | 37/50 [00:06<00:02,  5.60it/s]
   310/499     2.47G   0.03134    0.1004         0       799       640:  74%|#######4  | 37/50 [00:06<00:02,  5.60it/s]
   310/499     2.47G   0.03134    0.1004

   339/499     2.47G   0.03098   0.09777         0       737       640:  42%|####2     | 21/50 [00:03<00:04,  5.82it/s]
   339/499     2.47G   0.03088   0.09796         0       767       640:  42%|####2     | 21/50 [00:03<00:04,  5.82it/s]
   339/499     2.47G   0.03088   0.09796         0       767       640:  44%|####4     | 22/50 [00:03<00:04,  5.93it/s]
   339/499     2.47G   0.03094   0.09849         0       928       640:  44%|####4     | 22/50 [00:03<00:04,  5.93it/s]
   339/499     2.47G   0.03094   0.09849         0       928       640:  46%|####6     | 23/50 [00:03<00:04,  6.07it/s]
   339/499     2.47G   0.03101   0.09928         0       984       640:  46%|####6     | 23/50 [00:04<00:04,  6.07it/s]
   339/499     2.47G   0.03101   0.09928         0       984       640:  48%|####8     | 24/50 [00:04<00:04,  5.67it/s]
   339/499     2.47G   0.03096    0.0995         0       868       640:  48%|####8     | 24/50 [00:04<00:04,  5.67it/s]
   339/499     2.47G   0.03096    0.0995

                 all        306       7957      0.978      0.985      0.989      0.818
Results saved to runs\train\teeth4


# Test model

In [15]:
# run model again test image set
!python detect.py --weights runs/train/teeth/weights/best.pt --img 416 --conf 0.4 --source ../data/images/test/ --save-txt --save-conf

detect: weights=['runs/train/teeth/weights/best.pt'], source=../data/images/test/, imgsz=[416, 416], conf_thres=0.4, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=True, save_conf=True, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=runs\detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False
YOLOv5  v6.0-53-g5866646 torch 1.9.1+cu102 CUDA:0 (Quadro RTX 8000, 49152MiB)

Fusing layers... 
Model Summary: 232 layers, 7246518 parameters, 0 gradients
image 1/306 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\data\images\test\cate1-00003.jpg: 256x416 32 tooths, Done. (0.000s)
image 2/306 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\data\images\test\cate1-00008.jpg: 256x416 32 tooths, Done. (0.000s)
image 3/306 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\data

image 255/306 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\data\images\test\cate8-00361.jpg: 256x416 31 tooths, Done. (0.016s)
image 256/306 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\data\images\test\cate8-00363.jpg: 256x416 31 tooths, Done. (0.000s)
image 257/306 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\data\images\test\cate8-00365.jpg: 256x416 32 tooths, Done. (0.000s)
image 258/306 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\data\images\test\cate8-00366.jpg: 256x416 28 tooths, Done. (0.016s)
image 259/306 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\data\images\test\cate8-00369.jpg: 256x416 30 tooths, Done. (0.016s)
image 260/306 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\data\images\test\cate8-00373.jpg: 256x416 28 tooths, Done. (0.000s)
image 261/306 C:\Users\dental-1\Documents\dent

In [10]:
# run model against images in unseen image folder
!python detect.py --weights runs/train/teeth/weights/best.pt --img 416 --conf 0.4 --source ../unseen_images/ --save-txt --save-conf

detect: weights=['runs/train/teeth/weights/best.pt'], source=../unseen_images/, imgsz=[416, 416], conf_thres=0.4, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=True, save_conf=True, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=runs\detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False
YOLOv5  v6.0-53-g5866646 torch 1.9.1+cu102 CUDA:0 (Quadro RTX 8000, 49152MiB)

Fusing layers... 
Model Summary: 232 layers, 7246518 parameters, 0 gradients
image 1/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\1.2.840.114257.1.1637304243952960394983328788351918369.png: 256x416 28 tooths, Done. (0.016s)
image 2/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\1.2.840.114257.1.1637304243990896685435388404484448664.png: 256x416 28 tooths, Done. (0.016s)
image 3/1403 C

image 353/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\1.2.840.114257.3.6.21904647424457000458717898278835127461727.png: 224x416 23 tooths, Done. (0.016s)
image 354/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\1.2.840.114257.3.6.21927242640039600458502373000925572555825.png: 256x416 9 tooths, Done. (0.016s)
image 355/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\1.2.840.114257.3.6.21959904736462020458522177011614403127371.png: 256x416 29 tooths, Done. (0.016s)
image 356/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\1.2.840.114257.3.6.21992449552031670458414696369714082542947.png: 224x416 30 tooths, Done. (0.016s)
image 357/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\1.2.840.114257.3.6.21993051264471740458407746199512813619272.png: 224x4

In [17]:
# run model against specific image
!python detect.py --weights runs/train/teeth/weights/best.pt --conf 0.4 --source ../../2_dental_images/clahe_images/1.2.840.114257.3.6.10028842080465500458430592052923973032886.png --save-txt --save-conf


image 996/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\1.2.840.114257.3.6.33014659440040290458738430036944038406997.png: 256x416 30 tooths, Done. (0.016s)
image 997/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\1.2.840.114257.3.6.33015400384460090458515507208984473402628.png: 256x416 30 tooths, Done. (0.016s)
image 998/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\1.2.840.114257.3.6.33046354448204560458501119076482856212679.png: 256x416 30 tooths, Done. (0.016s)
image 999/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\cate2-00001.jpg: 256x416 30 tooths, Done. (0.016s)
image 1000/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_initial_tooth_segmentation\unseen_images\cate2-00002.jpg: 256x416 30 tooths, Done. (0.005s)
image 1001/1403 C:\Users\dental-1\Documents\dent_seg\4_train_yolo_

detect: weights=['runs/train/teeth/weights/best.pt'], source=../../2_dental_images/clahe_images/1.2.840.114257.3.6.10028842080465500458430592052923973032886.png, imgsz=[640, 640], conf_thres=0.4, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=True, save_conf=True, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=runs\detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False
YOLOv5  v6.0-53-g5866646 torch 1.9.1+cu102 CUDA:0 (Quadro RTX 8000, 49152MiB)

Fusing layers... 
Model Summary: 232 layers, 7246518 parameters, 0 gradients
image 1/1 C:\Users\dental-1\Documents\dent_seg\2_dental_images\clahe_images\1.2.840.114257.3.6.10028842080465500458430592052923973032886.png: 320x640 9 tooths, Done. (0.000s)
Speed: 0.0ms pre-process, 0.0ms inference, 15.6ms NMS per image at shape (1, 3, 640, 640)
Results saved to runs\detect\exp3
1 labels saved to runs\detect

In [4]:
# run model against specific image
!python detect.py --weights runs/train/teeth4/weights/best.pt --conf 0.4 --source ../../2_dental_images/raw_images/cate10-00050.jpg --save-txt --save-conf

detect: weights=['runs/train/teeth4/weights/best.pt'], source=../../2_dental_images/raw_images/cate10-00050.jpg, imgsz=[640, 640], conf_thres=0.4, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=True, save_conf=True, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=runs\detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False
YOLOv5  v6.0-53-g5866646 torch 1.9.1+cu102 CUDA:0 (Quadro RTX 8000, 49152MiB)

Fusing layers... 
Model Summary: 232 layers, 7246518 parameters, 0 gradients
image 1/1 C:\Users\dental-1\Documents\dent_seg\2_dental_images\raw_images\cate10-00050.jpg: 384x640 21 tooths, Done. (0.016s)
Speed: 0.0ms pre-process, 15.6ms inference, 0.0ms NMS per image at shape (1, 3, 640, 640)
Results saved to runs\detect\exp6
1 labels saved to runs\detect\exp6\labels
